# 3D Face Plot

Attenzione visualization

In [43]:
%load_ext autoreload
%autoreload 2
import os
from os.path import join
import sys
import time
import cv2 as cv
import numpy as np
import imutils
import matplotlib.animation
%matplotlib notebook
from glob import glob
from matplotlib import cbook
from matplotlib import cm
from matplotlib.colors import LightSource
from random import randint
sys.path.append('/megapixels/3rdparty/face-alignment')
import face_alignment
import numpy as np
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
import mpl_toolkits.mplot3d.axes3d as p3
from matplotlib import animation
import random
from skimage import io
from tqdm import tqdm_notebook as tqdm
from IPython.display import clear_output
from pathlib import Path


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [4]:
# Generate random hex colors
def rhex():
  r = lambda: random.randint(0,255)
  return '#%02X%02X%02X' % (r(), r(), r())

In [5]:
# init 3d face
# Run the 3D face alignment on a test image, without CUDA.
fa = face_alignment.FaceAlignment(face_alignment.LandmarksType._3D, 
                                  enable_cuda=True, flip_input=True)

In [6]:
data_bodega = '/megapixels/data_bodega/'
fp = join(data_bodega,'images/senators/*.jpg')
face_files = glob(fp,recursive=True)
print(len(face_files))

100


In [44]:
def generate_3d_face(fpath,output_dir):
  # load image
  im = io.imread(fpath)
  
  # generate 3d predictions
  preds = fa.get_landmarks(im)
  if preds is None:
    return
  preds = preds[-1]
  
  # plot style
  num_frames = 60
  lw = 2 # line weight
  bg_color = '#%02x%02x%02x' % (60,59,110)
  mark_clr = '#%02x%02x%02x' % (255,255,255) 
  mark_type='$\star$'
  mark_size = 20
  print(bg_color)
  
  dpi = 72
  figsize = (16,16)
  
  # center x,y,z
  xmm = (np.min(preds[:,0]),np.max(preds[:,0]))
  ymm = (np.min(preds[:,1]),np.max(preds[:,1]))
  zmm = (np.min(preds[:,2]),np.max(preds[:,2]))
  
  preds_orig = preds.copy()
  xmm_sc = (1.2*np.min(preds[:,0]),1.2*np.max(preds_orig[:,0]))
  xmm = (np.min(preds_orig[:,0]),np.max(preds_orig[:,0]))
  ymm = (np.min(preds_orig[:,1]),np.max(preds_orig[:,1]))
  zmm = (np.min(preds_orig[:,2]),np.max(preds_orig[:,2]))
  
  # swap the y and z components to improve 3d rotation angles
  preds = np.zeros_like(preds_orig).astype(np.uint8)
  for i,p in enumerate(preds_orig):
    x,y,z = p
    #preds[i] = np.array([x - xmm[0], y - ymm[0], z - zmm[0]]) # ?
    preds[i] = np.array([x - xmm[0], z - zmm[0], y - ymm[0]])
  
  # Create plot
  fig = plt.figure(figsize=figsize,dpi=dpi)
  fig.tight_layout()
  ax = fig.add_subplot(111, projection='3d')
  ax.set_facecolor(bg_color) # background color
  
  preds_plot = np.zeros_like(preds)
  for i,p in enumerate(preds):
    x,y,z = p
    preds_plot[i] = np.array([x,y,z])

  
  # scatter plot the dots
  ax.plot3D(preds_plot[:17,0]*1.2,preds_plot[:17,1], preds_plot[:17,2],
            marker=mark_type,markersize=mark_size,color=mark_clr,linewidth=lw)
  ax.plot3D(preds_plot[17:22,0]*1.2,preds_plot[17:22,1],preds_plot[17:22,2],
            marker=mark_type,markersize=mark_size,color=mark_clr,linewidth=lw)
  ax.plot3D(preds_plot[22:27,0]*1.2,preds_plot[22:27,1],preds_plot[22:27,2], 
            marker=mark_type,markersize=mark_size,color=mark_clr,linewidth=lw)
  ax.plot3D(preds_plot[27:31,0]*1.2,preds_plot[27:31,1],preds_plot[27:31,2],
            marker=mark_type,markersize=mark_size,color=mark_clr,linewidth=lw)
  ax.plot3D(preds_plot[31:36,0]*1.2,preds_plot[31:36,1],preds_plot[31:36,2],
            marker=mark_type,markersize=mark_size,color=mark_clr,linewidth=lw)
  ax.plot3D(preds_plot[36:42,0]*1.2,preds_plot[36:42,1],preds_plot[36:42,2],
            marker=mark_type,markersize=mark_size,color=mark_clr,linewidth=lw)
  ax.plot3D(preds_plot[42:48,0]*1.2,preds_plot[42:48,1],preds_plot[42:48,2],
            marker=mark_type,markersize=mark_size,color=mark_clr,linewidth=lw)
  ax.plot3D(preds_plot[48:,0]*1.2,preds_plot[48:,1],preds_plot[48:,2],
            marker=mark_type,markersize=mark_size,color=mark_clr, linewidth=lw)

  
  rh = '#ffffff'
  ax.scatter(preds_plot[:,0]*1.2,preds_plot[:,1],preds_plot[:,2],c=rh, alpha=1.0, s=35, edgecolor=rh)
  
  # center points
  cx = ((xmm[0] - xmm[1]) // 2) + xmm[1]
  cy = ((ymm[1] - ymm[0]) // 2) + ymm[0]
  cz = ((zmm[1] - zmm[0]) // 2) + zmm[0]

  #xpts = [cx,cx]
  #ypts = [cy,cy]
  #zpts = [zmm[0],zmm[1]]

  ax.view_init(elev=120., azim=70.)
  
  ax.set_xticks([])
  ax.set_yticks([])
  ax.set_zticks([])
  ax.set_axis_off()
  ax.set_xlabel('x')
  ax.set_ylabel('y')
  ax.set_zlabel('z')

  # write animation to disk
  fname_out = join(output_dir, '{}.gif'.format(Path(fpath).stem))
  print(fname_out)
  # rotation increments
  phi = np.linspace(0, 2*np.pi, num_frames)

  def update(phi):
      ax.view_init(180,phi*180./np.pi)
  
  ani = matplotlib.animation.FuncAnimation(fig, update, frames=phi)
  ani.save(fname_out, writer='imagemagick', fps=10)
  #del ani

In [47]:
output_dir = join(data_bodega,'output','senators_3d_points')

In [49]:
for f in tqdm(face_files):
  generate_3d_face(f,output_dir)
  clear_output()

In [ ]:
cv.L